In [1]:
import pandas as pd
import numpy as np
import os
import re
import string
import nltk
import emoji
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
# !pip uninstall certifi -y
# !pip install --no-cache-dir certifi==2025.7.14

from textacy import preprocessing as tprep
from tqdm import tqdm
tqdm.pandas()


pd.options.display.max_rows = 15


In [114]:
# Article Dataframe
article_df = pd.read_csv('/Users/amalkurian/Desktop/Dissertation/Bias Detection/Data/matching_articles04.csv')
print(f'List all the columns{list(article_df.columns)}')
# Events Datafrane
events_df = pd.read_csv('/Users/amalkurian/Desktop/Dissertation/Bias Detection/diffbot-export-tigray-war.csv')
print(f'List all the columns{list(events_df.columns)}')

List all the columns['doc_id', 'doc_id.1', 'doc_id.2', 'doc_id.3', 'doc_id.4', 'title', 'author', 'source', 'content', 'topic', 'url', 'keywords', 'query', 'cleaned_content', 'entities', 'article_id', 'entities_Group', 'labels_Group', 'Key_Phrases', 'Actions', 'Load_Date', 'Language', 'Person', 'matching_events', 'character_count', 'word_count', 'processed_text', 'processed_tokens_split', 'num_tokens', 'story_chain', 'match_score_faiss', 'temporal_scores', 'temporal_exp_score', 'temporal_log_score', 'match_score_Title', 'event_similarity_id_Title', 'match_label_x', 'match_label_y', 'match_label', 'actor_entities', 'geo_entities', 'entity_similarity', 'final_scores', 'max_score_index', 'match_Labels', 'Top_event_id', 'Top_event_title']
List all the columns['title', 'date_str', 'author', 'icon', 'siteName', 'tags_label', 'text', 'sentiment', 'pageUrl', 'quotes_quote']


In [115]:
article_df['Load_Date'] = pd.to_datetime(article_df['Load_Date'])

In [116]:
import hashlib

def generate_event_id(row):
    raw_String = f"{row['date_str']}_{row['title']}_{row['author']}"
    return hashlib.sha256(raw_String.encode('utf-8')).hexdigest()


events_df['event_id'] = events_df.progress_apply(generate_event_id, axis=1)



  0%|          | 0/2510 [00:00<?, ?it/s]

100%|██████████| 2510/2510 [00:00<00:00, 15955.13it/s]


In [117]:
events_df.tail()

title date_str  \
2505  وكانت العلاقات بين البلدين حينها ""سمنا على عس...      NaN   
2506  أحببت مشاركة هذه التجربة الشخصية لأنها ارتبطت ...      NaN   
2507  وسأفترض أن الحليفين سيخرجان منتصرين في الحرب، ...      NaN   
2508  الحليف والشريك اسياس يدخل الحرب، وهو شريك كامل...      NaN   
2509  وفي ظل المتغيرات المتسارعة من المرجح أيضا أن ت...      NaN   

                                         author icon siteName tags_label text  \
2505                                        NaN  NaN      NaN        NaN  NaN   
2506                                        NaN  NaN      NaN        NaN  NaN   
2507                                        NaN  NaN      NaN        NaN  NaN   
2508                                        NaN  NaN      NaN        NaN  NaN   
2509  https://www.adoulis.net/entry.php?id=6178  NaN      NaN        NaN  NaN   

      sentiment pageUrl quotes_quote  \
2505        NaN     NaN          NaN   
2506        NaN     NaN          NaN   
2507        NaN     NaN          NaN   
2508        NaN     NaN          NaN   
2509        NaN     NaN          NaN   

                                               event_id  
2505  aa9c337901539e9c2f04d0d1e47dc94b12f4163c81acb0...  
2506  f5c8dc4a5b76947a8b7296f390e5c04446a714ace40f99...  
2507  714380791f4677d8274c9f0b844e97b4a2079c2617b57f...  
2508  915684cff66d3304da59f2ac3660cec660142059401d32...  
2509  b85d84c20d3419fc0942a3fc8a59c6d53eb8b704372741...

In [139]:
import spacy
from tqdm.auto import tqdm

nlp = spacy.load("en_core_web_sm")

def extract_entities(text):
    doc = nlp(text) # gets the entities in the text
    entities = [(ent.text, ent.label_) for ent in doc.ents]
    return entities

# Events Dataframe: Extracting Entities using Spacy
# Character count has to be less than 1 million to avoid memory issues

def safe_extract(text):
    if isinstance(text, str) and len(text) < 1_000_000:
        return extract_entities(text)
    return []


events_df['entities'] = events_df['text'].progress_apply(safe_extract)
# Explode the entities For Events Dataframe
events_entities_long = events_df[['event_id', 'entities']].explode('entities')
# # Extract entity text and label
events_entities_long[['entity_text', 'label']] = pd.DataFrame(
    events_entities_long['entities'].tolist(), index=events_entities_long.index
)


100%|██████████| 2510/2510 [11:11<00:00,  3.74it/s]


In [158]:
events_df.columns

Index(['title', 'date_str', 'author', 'icon', 'siteName', 'tags_label', 'text',
       'sentiment', 'pageUrl', 'quotes_quote', 'event_id', 'entities'],
      dtype='object')

In [159]:
grouped_entities = (events_entities_long
        .groupby('event_id')
        .agg({
            'entity_text': lambda x: list(x),
            'label': lambda x: list(x)
        })
        .rename(columns={
            'entity_text': 'entities_Group', 'label': 'labels_Group'})
        )

events_df = events_df.merge(grouped_entities, on='event_id', how='left')


In [ ]:
events_df = events_df.rename(columns = {'label_Group_y': 'label_Group'})

In [136]:
# Format the date extracted into DateTime format %Y-%m-%d

events_df['date_str'] = (
    events_df['date_str']
    .str.replace(r'^d','',regex=True)
)

events_df['date_str'] = events_df['date_str'].str.split('T').str[0] # str is an accessor for string operations on Series
events_df['date_str'] = pd.to_datetime(events_df['date_str'], format='%Y-%m-%d', errors='coerce')
events_df['date_str'].head()

0   2022-10-10
1   2022-10-16
2   2022-10-12
3   2022-10-13
4   2022-12-14
Name: date_str, dtype: datetime64[ns]

In [162]:
from collections import Counter
import ast

def flatten_entities(col):
    flattened = []
    for ents in col:
        if not isinstance(ents, list):
            continue  # Skip NaNs or weird types
        for item in ents:
            if isinstance(item, (list, tuple)) and len(item) == 2:
                ent, label = item
                if label in {"ORG", "GPE", "PERSON", "NORP", "LOC"}:
                    flattened.append(ent)
    return flattened

# Flatten the entities and count occurances for Article Dataframe   
article_df['entities'] = article_df['entities'].apply(ast.literal_eval) 
all_entities = flatten_entities(article_df['entities'])

# Flatten the entities and count occurrences for Events Dataframe
all_events_entities = flatten_entities(events_df['entities'])

entity_counter = Counter(all_entities)
entity_events_counter = Counter(all_events_entities)

In [161]:
print(article_df['entities'].head(5))

0    [('October', 'DATE'), ('Ethiopian', 'NORP'), (...
1    [('Eritrea', 'GPE'), ('Ethiopia', 'GPE'), ('No...
2    [('Ethiopia', 'GPE'), ('Afar', 'GPE'), ('Sunda...
3    [('Ethiopia', 'GPE'), ('six-month', 'DATE'), (...
4    [('March', 'DATE'), ('early October', 'DATE'),...
Name: entities, dtype: object


In [163]:
# Raw Entities From Article Dataframe
threshold = 10
raw_ethiopia_entities = ((entity, count) for entity, count in entity_counter.most_common() if count >= threshold)
raw_events_entities = ((entity, count) for entity, count in entity_events_counter.most_common() if count >= threshold)
raw_events_entities = list(raw_events_entities)
raw_ethiopia_entities = list(raw_ethiopia_entities)

In [ ]:
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.cluster import AgglomerativeClustering

def mapping_events_entities(raw_entities):
    events_entities = list(e[0].lower() for e in raw_entities)
    model = SentenceTransformer('all-MiniLM-L6-v2')

    print('Encoding Entities...') 
    events_embeddings = model.encode(events_entities, show_progress_bar = True)
    events_similarity_matrix = cosine_similarity(events_embeddings)

    clustering = AgglomerativeClustering(
        n_clusters = None,
        metric = 'precomputed',
        linkage = 'complete',
        distance_threshold = 0.3)
    
    events_distance_matrix = 1 - events_similarity_matrix
    events_distance_matrix = events_distance_matrix.astype(np.float64)  # Convert to float32 for HDBSCAN compatibility
    labels = clustering.fit_predict(events_distance_matrix)  # position of the entities in the similarity/distance matrix closer the entity, smaller the distance

    events_cluster_df = pd.DataFrame({'entity': events_entities, 'cluster': labels}) # labels are used to create a list of similar entities and the most common entities will be extracted for the canonical term
    events_canonical_entities = {}

    for cluster_id, group in events_cluster_df.groupby('cluster'):
        # Choose the most common name as canonical
        canonical = Counter(group['entity']).most_common(1)[0][0]
        # canonical = sorted(group['entity'], key=lambda x: len(x))[0]
        for ent in group['entity']:
            events_canonical_entities[ent] = canonical
    
    mapping_events_entities = [(ent, events_canonical_entities[ent]) for ent in events_entities]
    return mapping_events_entities #tuple


# Generate the mapping for events entities
mapping_lookup_events_entities = mapping_events_entities(raw_events_entities)
for original, canonical in mapping_lookup_events_entities[:500]:
    print(f"{original} → {canonical}")

Encoding Entities...


Batches: 100%|██████████| 75/75 [00:07<00:00, 10.52it/s]


ethiopia → ethiopia
tigray → tigray
ethiopian → ethiopian
eritrea → eritrea
eritrean → eritrea
sudan → sudan
africa → africa
tplf → tplf
us → the united states
tigrayan → tigrayan
u.s. → the united states
china → china
addis ababa → addis ababa
un → un
somalia → somalia
russia → russia
amhara → the amhara association of america
african → african
abiy ahmed → abiy ahmed
tigrayans → tigrayan
ukraine → ukraine
ap → ap
biden → biden
kenya → nairobi
somali → somali
u.n. → u.n.
egypt → egypt
the united states → the united states
covid-19 → covid
reuters → reuters
russian → russian
au → au
oromo → oromo
the horn of africa → the horn of africa
sudanese → sudanese
spotify → spotify
mekelle → mekelle
apple → apple
afar → afar
oromia → oromia
blinken → blinken
ethiopians → ethiopian
eu → the european union
iran → iran
washington → washington
chinese → chinese
crisis group’s → the international crisis group
the associated press → the associated press
the african union → the african union
turkey → 

In [164]:
raw_ethiopia_entities

[('Ethiopia', 13749),
 ('Tigray', 9311),
 ('Ethiopian', 7151),
 ('TPLF', 7096),
 ('ETHIOPIA', 5039),
 ('Eritrea', 3091),
 ('Eritrean', 2911),
 ('Load-Date', 2869),
 ('Addis Ababa', 2417),
 ('US', 2264),
 ('Abiy Ahmed', 2140),
 ("the Tigray People's Liberation Front", 2088),
 ('Sudan', 2045),
 ('NEGATIVE NEWS', 1996),
 ('AFRICA', 1972),
 ('Amhara', 1962),
 ('WAR & CONFLICT', 1922),
 ('HEADS OF STATE & GOVERNMENT', 1915),
 ('UN', 1889),
 ('Tigrayan', 1844),
 ('UNITED NATIONS', 1833),
 ('ABIY AHMED', 1770),
 ('Mekelle', 1481),
 ('GOVERNMENT & PUBLIC ADMINISTRATION', 1475),
 ('Afar', 1194),
 ('UNITED STATES', 1131),
 ('CEASEFIRES', 1107),
 ('INTERNATIONAL RELATIONS', 1106),
 ('Ethiopians', 969),
 ('Africa', 899),
 ('U.S.', 825),
 ('NEGATIVE MISC NEWS', 808),
 ('KENYA', 796),
 ('Somalia', 790),
 ('EASTERN AFRICA', 745),
 ('Tigrayans', 741),
 ('INTERNATIONAL RELATIONS & NATIONAL SECURITY', 710),
 ('Kenya', 708),
 ('GOVERNMENT ADVISORS & MINISTERS', 705),
 ('STATE DEPARTMENTS & FOREIGN SERVIC

In [ ]:
mapping_lookup_articles_entities = mapping_events_entities(raw_ethiopia_entities)
for original, canonical in mapping_lookup_articles_entities[:500]:
    print(f"{original} → {canonical}")

Encoding Entities...


Batches: 100%|██████████| 48/48 [00:06<00:00,  7.98it/s]


ethiopia → ethiopia
tigray → tigray
ethiopian → ethiopia
tplf → tplf
ethiopia → ethiopia
eritrea → eritrea
eritrean → eritrea
load-date → load-date
addis ababa → addis ababa
us → america
abiy ahmed → abiy ahmed
the tigray people's liberation front → the tigray people's liberation front
sudan → sudan
negative news → negative news
africa → africa
amhara → amhara
war & conflict → war & conflict
heads of state & government → heads of state & government
un → un
tigrayan → tigray
united nations → united nations
abiy ahmed → abiy ahmed
mekelle → mekelle
government & public administration → government & public administration
afar → afar
united states → united states
ceasefires → ceasefires
international relations → international relations
ethiopians → ethiopia
africa → africa
u.s. → united states
negative misc news → negative news
kenya → nairobi
somalia → somalia
eastern africa → africa
tigrayans → tigray
international relations & national security → international relations
kenya → nairobi
go

In [ ]:
mapped_articles_entities_dictionary = dict(mapping_lookup_articles_entities)
mapped_events_entities_dictionary = dict(mapping_lookup_events_entities)

In [165]:
# Normalize the entities in the articles and events Dataframe
# !pip install rapidfuzz

from rapidfuzz import process

def normalize_entity(ent, entity_mapping, threshold=90): # for spelling mistakes for canonical entities
    if not isinstance(ent, str) or not ent.strip():
        return ent
    match, score, _ = process.extractOne(
        ent.lower(), entity_mapping.keys()
    )

    return entity_mapping[match] if match else ent 


# Events Entities Normalization
normalized_events_entities = [normalize_entity(ent,mapped_events_entities_dictionary) for ent,_ in raw_events_entities]
normalized_events_entities[:50]  # Display first 50 normalized entities
# Normalize the entities in the articles 
normalized_articles_entities = [normalize_entity(ent,mapped_articles_entities_dictionary) for ent,_ in raw_ethiopia_entities]
normalized_articles_entities[:50]  # Display first 50 normalized entities

['ethiopia',
 'tigray',
 'ethiopia',
 'tplf',
 'ethiopia',
 'eritrea',
 'eritrea',
 'load-date',
 'addis ababa',
 'america',
 'abiy ahmed',
 "the tigray people's liberation front",
 'sudan',
 'negative news',
 'africa',
 'amhara',
 'war & conflict',
 'heads of state & government',
 'un',
 'tigray',
 'united nations',
 'abiy ahmed',
 'mekelle',
 'government & public administration',
 'afar',
 'united states',
 'ceasefires',
 'international relations',
 'ethiopia',
 'africa',
 'united states',
 'negative news',
 'nairobi',
 'somalia',
 'africa',
 'tigray',
 'international relations',
 'nairobi',
 'government advisors & ministers',
 'state departments & foreign services',
 'talks & meetings',
 'united states',
 "the tigray people's liberation front",
 'the african union',
 'african',
 'law enforcement & corrections',
 'government bodies & offices',
 'international relations',
 'mekele',
 'south africa']

In [166]:
events_entities_long['normalized'] = events_entities_long.progress_apply(lambda x: normalize_entity(x['entity_text'], mapped_events_entities_dictionary), axis=1)

100%|██████████| 353985/353985 [28:53<00:00, 204.19it/s]


In [66]:

# Explode the entities
entities_long = article_df[['article_id', 'entities']].explode('entities')

# # Extract entity text and label
entities_long[['entity_text', 'label']] = pd.DataFrame(
    entities_long['entities'].tolist(), index=entities_long.index
    )
entities_long.head()



100%|██████████| 360576/360576 [24:13<00:00, 248.05it/s]


In [ ]:
entities_long['normalized'] = entities_long.progress_apply(lambda x: normalize_entity(x['entity_text'], mapped_articles_entities_dictionary), axis = 1)

In [67]:
actor_types = ['PERSON', 'ORG', 'NORP']
geo_types = ['GPE', 'LOC']
actor_df = entities_long[entities_long['label'].isin(actor_types)] \
    .groupby('article_id')['normalized'].apply(set).reset_index(name='actor_entities')
geo_df = entities_long[entities_long['label'].isin(geo_types)] \
    .groupby('article_id')['normalized'].apply(set).reset_index(name='geo_entities')
# Merge actor and geo entities
merged_df = pd.merge(actor_df, geo_df, on='article_id', how='outer')
# Merge cleanly
article_df = article_df.merge(merged_df, on='article_id', how='left')


In [169]:
actor_types = ['PERSON', 'ORG', 'NORP']
geo_types = ['GPE', 'LOC']

actor_df = events_entities_long[events_entities_long['label'].isin(actor_types)] \
    .groupby('event_id')['normalized'].apply(set).reset_index(name='actor_entities')

geo_df = events_entities_long[events_entities_long['label'].isin(geo_types)] \
    .groupby('event_id')['normalized'].apply(set).reset_index(name='geo_entities')

# Merge actor and geo entities
merged_df = pd.merge(actor_df, geo_df, on='event_id', how='outer')


# Merge cleanly
events_df = events_df.merge(merged_df, on='event_id', how='left')


In [168]:
events_df.columns 


Index(['title', 'date_str', 'author', 'icon', 'siteName', 'tags_label', 'text',
       'sentiment', 'pageUrl', 'quotes_quote', 'event_id', 'entities',
       'entities_Group', 'labels_Group'],
      dtype='object')

In [180]:
# Filter events for each article based on the date range

from datetime import timedelta

delta = timedelta(days=7)

def filter_events_for_article(Article_date):
    
    lower = Article_date - timedelta(days=27)
    upper = Article_date + timedelta(days=7) 
    filtered = events_df[events_df['date_str'].between(lower, upper)] # it is a DataFrame
    return filtered['event_id'].tolist()


article_df['Load_Date'] = pd.to_datetime(article_df['Load_Date'])
article_df['Load_Date'].head()

article_df['matching_events'] = article_df['Load_Date'].progress_apply(filter_events_for_article)


100%|██████████| 3322/3322 [00:05<00:00, 660.82it/s]


# Entity Similarity Scores

In [186]:
def safe_set(x):
    if isinstance(x, set):
        return x
    if isinstance(x, list):
        return set(x)
    if pd.isna(x) or not x:
        return set()
    if isinstance(x, str):
        try:
            # Safely parse string literal like "{a, b, c}" into set
            parsed = ast.literal_eval(x)
            # parsed might be set, list, tuple — convert to set
            return set(parsed)
        except (ValueError, SyntaxError):
            # Fallback: split by commas if parsing fails
            return set(e.strip() for e in x.strip('{}').split(',') if e.strip())
    return set([x])

def compute_entity_similarity(article_actors, article_geos, event_actors, event_geos):
    # Sanitize inputs
    article_actors = safe_set(article_actors)
    event_actors = safe_set(event_actors)
    article_geos = safe_set(article_geos)
    event_geos = safe_set(event_geos)
    
    actor_score = (
        len(article_actors & event_actors) / len(event_actors | article_actors)
        if event_actors else 0
    )
    geo_score = (
        len(article_geos & event_geos) / len(event_geos | article_geos)
        if event_geos else 0
    )
    return actor_score, geo_score

similarity_scores = []

# Convert events_df into a quick lookup dict for speed
event_lookup = {
    row['event_id']: row
    for _, row in events_df.iterrows()
}

for _, article_row in article_df.iterrows():
    article_id = article_row['article_id']
    a_actors = article_row['actor_entities']
    a_geos = article_row['geo_entities']
    
    # Get pre-filtered event IDs for this article
    matching_events = article_row.get('matching_events', [])

    for event_id in matching_events:
        # Defensive check: skip if event_id not in lookup
        
        if event_id not in event_lookup:
            continue

        event_row = event_lookup[event_id]
        e_actors = event_row['actor_entities']
        e_geos = event_row['geo_entities']
        
        # Compute similarity
        actor_score, geo_score = compute_entity_similarity(a_actors, a_geos, e_actors, e_geos)
        print(actor_score)
        similarity_scores.append({
            'article_id': article_id,
            'event_id': event_id,
            'actor_score': actor_score,
            'geo_score': geo_score,
            'combined_score': (actor_score + geo_score) / 2  # or weighted
        })



0.0
0.0
0.046875
0.033707865168539325
0.09243697478991597
0.06369426751592357
0.024390243902439025
0.033707865168539325
0.05063291139240506
0.0125
0.02857142857142857
0.012345679012345678
0.014084507042253521
0.0
0.0410958904109589
0.05194805194805195
0.03896103896103896
0.06493506493506493
0.04878048780487805
0.0684931506849315
0.07228915662650602
0.04411764705882353
0.07042253521126761
0.05319148936170213
0.0547945205479452
0.043478260869565216
0.05714285714285714
0.031578947368421054
0.06578947368421052
0.02459016393442623
0.05714285714285714
0.06756756756756757
0.06493506493506493
0.031578947368421054
0.06666666666666667
0.0547945205479452
0.05319148936170213
0.07042253521126761
0.04411764705882353
0.0759493670886076
0.06666666666666667
0.04411764705882353
0.04
0.04285714285714286
0.06329113924050633
0.06756756756756757
0.0684931506849315
0.03225806451612903
0.038461538461538464
0.02702702702702703
0.0
0.06666666666666667
0.03296703296703297
0.06666666666666667
0.0684931506849315
0

In [188]:
to_find_combined_score = pd.DataFrame(similarity_scores)

In [189]:
to_find_combined_score

article_id                                           event_id  \
0                0  2c92c68e655d3678c72144993416a978c0b712596d1b52...   
1                0  7acbfb9edb8a68427726bd24ac1221174ce8bfd40698f3...   
2                0  3d3536a1334cf71bd4332e19b1ab7b8816f5e65905cc6a...   
3                0  f4fd207f045f01ef1407b6a5c3bb40faa4280a4b8e003b...   
4                0  ee82725f914bf018569d393856e4f4611a81bcb25584de...   
...            ...                                                ...   
275006        3320  75571a7d4cce072f9e1a71b7d1b53c7a6af1961f2ec817...   
275007        3320  40a73658460f863d6a00dd8b834724402327c3652aea3f...   
275008        3320  2fe2b7a7cad9f7f888bf7f0b62e109aa77983fc28bbb02...   
275009        3320  b378035eaa85afbc1031c8ef3448537c17b2328eed82fe...   
275010        3320  c43f905b9ee38fd32508000713405a7ee3a4bad325c399...   

        actor_score  geo_score  combined_score  
0          0.000000   0.093750        0.046875  
1          0.000000   0.040000        0.020000  
2          0.046875   0.031250        0.039062  
3          0.033708   0.111111        0.072409  
4          0.092437   0.176471        0.134454  
...             ...        ...             ...  
275006     0.027778   0.142857        0.085317  
275007     0.024000   0.000000        0.012000  
275008     0.025641   0.000000        0.012821  
275009     0.027027   0.000000        0.013514  
275010     0.021277   0.090909        0.056093  

[275011 rows x 5 columns]

In [192]:
# With Cosine Similarity

from transformers import AutoTokenizer
from sentence_transformers import SentenceTransformer, util
from nltk.tokenize import sent_tokenize
import nltk
import torch
import pandas as pd

#nltk.download('punkt')

model = SentenceTransformer("BAAI/bge-base-en-v1.5")  # or 'bge-large-en-v1.5'

# article_df['cleaned_content']
# article_df['matching_events'] = list of event_ids within same time window
# events_df['event_id'], events_df['text']


# Event embedding index (for fast lookup)
events_df['title'] = events_df['title'].fillna('').astype(str)
events_id_to_vector = {
    row['event_id']: model.encode(row['title'], convert_to_tensor=True, batch_size=32, show_progress_bar=False)
    for _, row in events_df.iterrows()
}

# --- Function to embed and average article sentences
def embed_article_sentences(text):
    sentences = sent_tokenize(text)
    if not sentences:
        return torch.zeros(model.get_sentence_embedding_dimension())
    sentence_embeddings = model.encode(sentences, convert_to_tensor=True, batch_size=32, show_progress_bar=False)
    return torch.mean(sentence_embeddings, dim=0) # gets you a single embedding for the whole paragraph by finding the mean

# compare only against its matching_events
article_match_scores = []
article_match_ids = []

for idx, row in article_df.iterrows():
    article_vec = embed_article_sentences(row.title)

    matching_event_ids = row.get('matching_events', [])
    if not matching_event_ids:
        article_match_scores.append(None)
        article_match_ids.append(None)
        continue

    # Get event vectors for those in the matching time window
    event_vecs = [events_id_to_vector[eid] for eid in matching_event_ids if eid in events_id_to_vector]
    
    if not event_vecs:
        article_match_scores.append(None)
        article_match_ids.append(None)
        continue

    event_tensor = torch.stack(event_vecs) # create a 2D matrix for cosine similarity, it won't work on a list

    # Cosine similarity
    sim_scores = util.cos_sim(article_vec, event_tensor).squeeze(0)  # Shape: [num_events]
    
    scores_list = sim_scores.tolist()

    article_match_scores.append(scores_list)
    article_match_ids.append(matching_event_ids)

# Attach to DataFrame
article_df['match_score_Title'] = article_match_scores
article_df['event_similarity_id_Title'] = article_match_ids


In [193]:
# Explode article_df lists into one row per event_id and score
exploded = article_df.explode(['event_similarity_id_title', 'match_score_Title']).rename(columns={
    'event_similarity_id_title': 'event_id',
    'match_score_Title': 'match_score'
})


['2c92c68e655d3678c72144993416a978c0b712596d1b524d6523e987e37e0f41',
 '7acbfb9edb8a68427726bd24ac1221174ce8bfd40698f33ffeda58bdb851de0c',
 '3d3536a1334cf71bd4332e19b1ab7b8816f5e65905cc6ab9b418aa5f516b42be',
 'f4fd207f045f01ef1407b6a5c3bb40faa4280a4b8e003bdaf48ebcea66c22308',
 'ee82725f914bf018569d393856e4f4611a81bcb25584de168de24551542315b0',
 'a54baec7313e5beaa0376575fbd012f6af0797209a560dffc5b045e5eef5827e',
 '3ee64f118c767996b1b2cd6f96fc769e74da9210f5147a65c5a14be73a2d33b9',
 'e2a006f0781c07aa1204d6e99f502f057abad17c462d273ca5f9680fe734b78c',
 'f406d6cf6ef2d101af4b58450d1b34e7b7a4e56e6e4382b954c98a3645f13d9e',
 'd7da99b4eb2b16ca86349cd3f3b1a13fb8e2f06cd7e5ee665e6066204ab34885',
 'df0a87c8f86154406377ac79fbd95ca7483ea384d5bf7b254fb302c8d5592d44',
 '03e55af0ca2c5b4853e6852a6b6aacfe90ce9888cb74b6b2c13b9fec3825f34e',
 '371b913000ef627cd0ef9671426fabf71ea00fa6eacd9f1666b10229637f9e41',
 '3e231f1f8c415013fd0eb656ff2cae75f60320b470c643686ecd35c1b5b6e2bd',
 '438ea15f2a8cf44ff4a94b5671adf291

In [194]:
to_find_combined_score

article_id                                           event_id  \
0                0  2c92c68e655d3678c72144993416a978c0b712596d1b52...   
1                0  7acbfb9edb8a68427726bd24ac1221174ce8bfd40698f3...   
2                0  3d3536a1334cf71bd4332e19b1ab7b8816f5e65905cc6a...   
3                0  f4fd207f045f01ef1407b6a5c3bb40faa4280a4b8e003b...   
4                0  ee82725f914bf018569d393856e4f4611a81bcb25584de...   
...            ...                                                ...   
275006        3320  75571a7d4cce072f9e1a71b7d1b53c7a6af1961f2ec817...   
275007        3320  40a73658460f863d6a00dd8b834724402327c3652aea3f...   
275008        3320  2fe2b7a7cad9f7f888bf7f0b62e109aa77983fc28bbb02...   
275009        3320  b378035eaa85afbc1031c8ef3448537c17b2328eed82fe...   
275010        3320  c43f905b9ee38fd32508000713405a7ee3a4bad325c399...   

        actor_score  geo_score  combined_score  
0          0.000000   0.093750        0.046875  
1          0.000000   0.040000        0.020000  
2          0.046875   0.031250        0.039062  
3          0.033708   0.111111        0.072409  
4          0.092437   0.176471        0.134454  
...             ...        ...             ...  
275006     0.027778   0.142857        0.085317  
275007     0.024000   0.000000        0.012000  
275008     0.025641   0.000000        0.012821  
275009     0.027027   0.000000        0.013514  
275010     0.021277   0.090909        0.056093  

[275011 rows x 5 columns]

In [199]:
# Explode the lists into rows for clean merging
exploded_article = article_df.explode(['event_similarity_id_Title', 'match_score_Title']).rename(columns={
    'event_similarity_id_Title': 'event_id',
    'match_score_Title': 'match_score'
})

# Merge on both article_id and event_id
merged_df = pd.merge(
    to_find_combined_score,
    exploded_article[['article_id', 'event_id', 'match_score']],
    on=['article_id', 'event_id'],
    how='left'
)

print(merged_df.head(2))


   article_id                                           event_id  actor_score  \
0           0  2c92c68e655d3678c72144993416a978c0b712596d1b52...          0.0   
1           0  7acbfb9edb8a68427726bd24ac1221174ce8bfd40698f3...          0.0   

   geo_score  combined_score match_score  
0    0.09375        0.046875    0.458419  
1    0.04000        0.020000    0.509666  


In [ ]:
merged_df

In [201]:
import pandas as pd
import numpy as np
from datetime import datetime
import math

# Convert to datetime if needed
article_df['Load_Date'] = pd.to_datetime(article_df['Load_Date'])
events_df['date_str'] = pd.to_datetime(events_df['date_str'])

# Params from the paper
alpha_h = 1.0  # for historical
alpha_p = 0.8  # for predictive
lambda_ = 0.8
max_past_days = 30
max_future_days = 10

# Convert events_df to a dict for fast lookup
event_date_lookup = dict(zip(events_df['event_id'], events_df['date_str']))

# Function to calculate temporal proximity 
# Distance from 0 is considered over negative or positive value
def compute_exp_temporal_score(pub_date, event_date):
    delta_days = (event_date - pub_date).days  # Positive if event after article (predictive)
    
    if delta_days > 0:
        # Predictive reporting
        decay = delta_days / max_future_days
        score = alpha_p * np.exp(-lambda_ * decay)
    else:
        # Historical reporting
        decay = abs(delta_days) / max_past_days
        score = alpha_h * np.exp(-lambda_ * decay)
    
    return round(score, 4)

def compute_log_temporal_score(pub_date, event_date):
    delta_days = abs((event_date - pub_date).days)

    if delta_days > 0:
        H = 10
    else:
        H = 30

    value = (delta_days + 1)/H
    inner = math.log(value)
    if inner <= 0.0:
        return 0.0
    
    score = -math.log(H * inner) / math.log(H)
    return round(score, 4)

# Apply to all article-event pairs
def compute_temporal_scores(row):
    pub_date = row['Load_Date']
    matching_events = row.get('matching_events', [])

    exp_scores = {}
    log_scores = {}

    for eid in matching_events:
        event_date = event_date_lookup.get(eid)

        if pd.notna(event_date):
            exp_score = compute_exp_temporal_score(pub_date, event_date)
            exp_scores[eid] = exp_score

            log_score = compute_log_temporal_score(pub_date, event_date)
            log_scores[eid] = log_score

    return {'exp': exp_scores, 'log': log_scores}

# Add temporal proximity scores to article_df
article_df['temporal_scores'] = article_df.apply(compute_temporal_scores, axis=1)


In [212]:
# Step 1: Merge the temporal_scores into the main df
merged_with_temp = merged_df.merge(article_df[['article_id', 'temporal_scores']], on='article_id', how='left')



In [214]:
def extract_exp(row):
    exp_dict = row['temporal_scores'].get('exp', {})
    return exp_dict.get(row['event_id'], np.nan)

merged_with_temp['temporal_score_exp'] = merged_with_temp.apply(extract_exp, axis=1)

In [216]:
merged_with_temp = merged_with_temp.drop(columns=['temporal_scores'])
merged_with_temp

article_id                                           event_id  \
0                0  2c92c68e655d3678c72144993416a978c0b712596d1b52...   
1                0  7acbfb9edb8a68427726bd24ac1221174ce8bfd40698f3...   
2                0  7acbfb9edb8a68427726bd24ac1221174ce8bfd40698f3...   
3                0  3d3536a1334cf71bd4332e19b1ab7b8816f5e65905cc6a...   
4                0  f4fd207f045f01ef1407b6a5c3bb40faa4280a4b8e003b...   
...            ...                                                ...   
439232        3320  75571a7d4cce072f9e1a71b7d1b53c7a6af1961f2ec817...   
439233        3320  40a73658460f863d6a00dd8b834724402327c3652aea3f...   
439234        3320  2fe2b7a7cad9f7f888bf7f0b62e109aa77983fc28bbb02...   
439235        3320  b378035eaa85afbc1031c8ef3448537c17b2328eed82fe...   
439236        3320  c43f905b9ee38fd32508000713405a7ee3a4bad325c399...   

        actor_score  geo_score  combined_score match_score  temporal_score_exp  
0          0.000000   0.093750        0.046875    0.458419              1.0000  
1          0.000000   0.040000        0.020000    0.509666              0.6293  
2          0.000000   0.040000        0.020000    0.509666              0.6293  
3          0.046875   0.031250        0.039062    0.406133              1.0000  
4          0.033708   0.111111        0.072409    0.532407              0.9737  
...             ...        ...             ...         ...                 ...  
439232     0.027778   0.142857        0.085317    0.365145              0.8297  
439233     0.024000   0.000000        0.012000    0.406265              0.8752  
439234     0.025641   0.000000        0.012821    0.419626              0.8752  
439235     0.027027   0.000000        0.013514    0.569073              0.8752  
439236     0.021277   0.090909        0.056093    0.395583              0.4570  

[439237 rows x 7 columns]

In [251]:
merged_with_temp['temporal_score_exp'].max()

1.0

In [293]:
import itertools


def normalize_score(score, min_val, max_val):
    return (score - min_val) / (max_val - min_val) if max_val > min_val else 0

def combined_score(row, weights, min_vals, max_vals):
    entity_ = normalize_score(row.get('combined_score', 0), min_vals['entity_similarity'], max_vals['entity_similarity'])
    temporal_ = normalize_score(row.get('temporal_score_exp', 0), min_vals['temporal_exp_score'], max_vals['temporal_exp_score'])
    semantic_ = normalize_score(row.get('match_score', 0), min_vals['text_similarity'], max_vals['text_similarity'])
    
    combined = (
        weights['semantic'] * semantic_ + 
        weights['entity'] * entity_ +
        weights['temporal'] * temporal_
    )
    return combined


def classify_match(score, threshold=0.45):
    return "Valid" if score >= threshold else "Invalid"


weights = {
    'semantic': 0.4,
    'entity': 0.4,
    'temporal': 0.2
}


min_vals = {
    'text_similarity': merged_with_temp['match_score'].min(),
    'entity_similarity': merged_with_temp['combined_score'].min(),
    'temporal_exp_score': merged_with_temp['temporal_score_exp'].min()
}

max_vals = {
    'text_similarity': merged_with_temp['match_score'].max(),
    'entity_similarity': merged_with_temp['combined_score'].max(),
    'temporal_exp_score': merged_with_temp['temporal_score_exp'].max()
}

merged_with_temp['final_scores'] = merged_with_temp.progress_apply(
    lambda row: combined_score(row, weights, min_vals, max_vals), axis=1)

merged_with_temp['match_Labels'] = merged_with_temp['final_scores'].progress_apply(classify_match)

100%|██████████| 439237/439237 [00:00<00:00, 615783.44it/s]


In [294]:
# For each article_id, find the max final_scores
max_scores = merged_with_temp.groupby('article_id')['final_scores'].transform('max')

# Filter rows where final_scores == max for that article_id
filtered_df = merged_with_temp[merged_with_temp['final_scores'] == max_scores].copy()
filtered_df

article_id                                           event_id  \
30               0  4dc83fb671cf9902099e6f44157eb4ad50c7b91390f909...   
319              1  534b3154c9b2170b43d067f18256b357859176de9c47f3...   
461              2  56222e8f00be3dd620eb8c4e9563443c75827d576cd8c6...   
536              3  e1ff6111870749dc616769907ae0b3e7c8c0b294f2d060...   
560              3  c06effe7c880cb02265799d83ac03f28554a382cf387e8...   
...            ...                                                ...   
438619        3316  56222e8f00be3dd620eb8c4e9563443c75827d576cd8c6...   
439034        3317  cc48da3e947769a367154b51bdf247ffa4f90a25bebd4a...   
439071        3318  2270763ecb38a00674d8cedb74ca936129d7b8e54a36af...   
439121        3319  0978c01466be702b312c563a2db9f68acc006cc521d53f...   
439187        3320  286d5c391d7d4ef9f6cc03e94862b194d9701ca60d9dbe...   

        actor_score  geo_score  combined_score match_score  \
30         0.072289   0.320000        0.196145    0.646742   
319        0.093750   0.250000        0.171875    0.791332   
461        0.171429   0.400000        0.285714    0.912512   
536        0.060606   1.000000        0.530303    0.580695   
560        0.060606   1.000000        0.530303    0.580695   
...             ...        ...             ...         ...   
438619     0.172414   0.142857        0.157635     0.50398   
439034     0.093023   0.333333        0.213178     0.96021   
439071     0.054795   0.214286        0.134540    0.588723   
439121     0.073171   0.333333        0.203252    0.605934   
439187     0.130435   0.153846        0.142140    0.579697   

        temporal_score_exp  final_scores match_Labels  
30                  0.9737      0.546709        Valid  
319                 0.7261      0.508367        Valid  
461                 0.7385      0.641095        Valid  
536                 0.5809      0.579807        Valid  
560                 0.5809      0.579807        Valid  
...                    ...           ...          ...  
438619              1.0000      0.465163        Valid  
439034              0.9737      0.704830        Valid  
439071              1.0000      0.490597        Valid  
439121              0.9481      0.522523        Valid  
439187              0.9481      0.471985        Valid  

[5629 rows x 9 columns]

In [295]:
filtered_df['match_Labels'].value_counts()

match_Labels
Valid      4448
Invalid    1181
Name: count, dtype: int64

In [296]:
def deduplicate_keep_order(lst):
    seen = set()
    deduped = []
    for item in lst:
        if item not in seen:
            seen.add(item)
            deduped.append(item)
    return deduped

combined_df = filtered_df.groupby('article_id').agg({
    'event_id': lambda x: deduplicate_keep_order(list(x)),
    'actor_score': lambda x: deduplicate_keep_order(list(x)),
    'geo_score': lambda x: deduplicate_keep_order(list(x)),
    'combined_score': lambda x: deduplicate_keep_order(list(x)),
    'match_score': lambda x: deduplicate_keep_order(list(x)),
    'temporal_score_exp': lambda x: deduplicate_keep_order(list(x)),
    'final_scores': lambda x: deduplicate_keep_order(list(x)),
    'match_Labels': lambda x: deduplicate_keep_order(list(x))
}).reset_index()



In [297]:
combined_df['match_Labels'].value_counts()

match_Labels
[Valid]      2166
[Invalid]     580
Name: count, dtype: int64

In [274]:
article_df.columns

Index(['title', 'author', 'source', 'content', 'topic', 'url', 'keywords',
       'query', 'cleaned_content', 'entities', 'article_id', 'entities_Group',
       'labels_Group', 'Key_Phrases', 'Actions', 'Load_Date', 'Language',
       'Person', 'matching_events', 'character_count', 'word_count',
       'processed_text', 'processed_tokens_split', 'num_tokens', 'story_chain',
       'match_score_faiss', 'temporal_scores', 'temporal_exp_score',
       'temporal_log_score', 'actor_entities', 'geo_entities'],
      dtype='object')

In [ ]:
# Merge and bring over match_labels and any other columns from combined_df
article_df_merged = article_df.merge(combined_df, on='article_id', how='left')
# Fill 'match_labels' with 'Invalid' where it's NaN (i.e., no match from combined_df)
article_df_merged['match_Labels'] = article_df_merged['match_Labels'].fillna('Invalid')
article_df_merged['match_Labels'] = article_df_merged['match_Labels'].astype(str).str.strip("[]").str.strip("'")

In [304]:
article_df_merged['match_Labels'].value_counts()

match_Labels
Valid      2166
Invalid    1156
Name: count, dtype: int64

In [306]:
article_df_merged.to_csv("article_event_matches_merged.csv", index=False)

In [309]:
events_df.to_csv("events02_df.csv", index=False)